# RNN + LSTM Model

For our project we elected to do the Natural Language Generation task. We wanted to do something all group members had interest in so we had the idea to generate summaries for a Charlotte Hornets NBA Game. To do this we had to limit our corpus to just Hornets game but that did not go well in terms of generating a summary, it performed poorly. To fix that we chose to be more specific and limited to our corpus to just games that featured both the Hornets and Atlanta Hawks, we chose the Hawks since they play in the same division as the Hornets so there would be a good amount of text to use for our corpus. 

We made our final goal to be that we were gonna generate a model that would make an accurate Charlotte Hornets vs Atlanta Hawks summary. 

## Imports

In [ ]:
!pip install rouge

In [ ]:
!pip install rouge_score

In [ ]:
import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, Activation, Embedding, LSTM, Bidirectional, Flatten, Dropout, GRU, RNN
from keras.optimizers import RMSprop, Adam, SGD
from keras.callbacks import ModelCheckpoint
from keras.callbacks import ReduceLROnPlateau
from keras.callbacks import LambdaCallback

from google.colab import drive
import random
import numpy as np
import os
import time
import string
import json
import pandas as pd
import time
import math
import nltk
from nltk.translate.bleu_score import sentence_bleu
from nltk.translate.bleu_score import corpus_bleu
from nltk.translate.bleu_score import SmoothingFunction
#from nltk.metrics.scores import accuracy
from nltk import word_tokenize
from nltk.corpus import stopwords 
import rouge
from rouge_score import rouge_scorer

# run the line below once 
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

## Loads Data

In [ ]:
# Mounts Google Drive

drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df = pd.read_csv("/content/drive/My Drive/School/Natural Language Processing/NBA_Data.csv")
df

home_city  ...        date
0         New York  ...  12/25/2016
1          Phoenix  ...    4/4/2015
2         Portland  ...   3/28/2017
3      Los Angeles  ...   11/3/2014
4          Chicago  ...  12/19/2016
...            ...  ...         ...
4848        Denver  ...   3/13/2017
4849     Minnesota  ...   3/28/2016
4850      Portland  ...  10/28/2015
4851  Golden State  ...  12/20/2016
4852  Golden State  ...    1/6/2017

[4853 rows x 9 columns]

## Sets Up Data

Creates a Dictionary to Store the Home Teams

There will be thirty instances in this dictionary because there are thirty teams in the NBA

- **Key**: Home Team Name
- **Value**: A list of summaries for the games corelating to any instance where the Key is the Home Name

In [ ]:
home_team_dict = {
    "Hawks" : [],
    "Celtics" : [],
    "Nets" : [],
    "Hornets" : [],
    "Bulls" : [],
    "Cavaliers" : [],
    "Mavericks" : [],
    "Nuggets" : [],
    "Pistons" : [],
    "Warriors" : [],
    "Rockets" : [],
    "Pacers" : [],
    "Clippers" : [],
    "Lakers" : [],
    "Grizzlies" : [],
    "Heat" : [],
    "Bucks" : [],
    "Timberwolves" : [],
    "Pelicans" : [],
    "Knicks" : [],
    "Thunder" : [],
    "Magic" : [],
    "76ers" : [],
    "Suns" : [],
    "Trail Blazers" : [],
    "Kings" : [],
    "Spurs" : [],
    "Raptors" : [],
    "Jazz" : [],
    "Wizards" : []
}

In [ ]:
for team in home_team_dict:
    print(team, "→", home_team_dict[team])

Hawks → []
Celtics → []
Nets → []
Hornets → []
Bulls → []
Cavaliers → []
Mavericks → []
Nuggets → []
Pistons → []
Warriors → []
Rockets → []
Pacers → []
Clippers → []
Lakers → []
Grizzlies → []
Heat → []
Bucks → []
Timberwolves → []
Pelicans → []
Knicks → []
Thunder → []
Magic → []
76ers → []
Suns → []
Trail Blazers → []
Kings → []
Spurs → []
Raptors → []
Jazz → []
Wizards → []


### Stores the Data into the Dictionary

In [ ]:
# Used to iterate through the 30 teams
for key in home_team_dict:

    # Iterates through the df to add a summary for the key that represents a home team
    for col, row in df.iterrows():
        if(key == row["home_name"]):
            home_team_dict[key].append(row["summary"])

    print(str(key) + ":")
    print(home_team_dict[key])
    print()

Hawks:
["The Atlanta Hawks ( 49 - 12 ) asserted their dominance as the top team in the East on Friday by beating the fourth - place Cleveland Cavaliers ( 39 - 25 ) 106 - 97 on Friday . As usual , it was a team effort that gave the Hawks the win , with seven players finishing in double digits , including Dennis Schroder 's 15 points and eight assists in 24 minutes off the bench . Despite playing a somewhat limited role off the bench , Schroder has averaged 16 points and 9 assists in just 29 minutes per game over his last three outings . The Hawks do n't have an MVP candidate on their roster , but if they keep beating the other top teams in the NBA , it makes the idea of extending the Player of the Month Award that was given to the entire starting five for their perfect 170 run in January an intriguing notion to suggest for the MVP award that is historically only given to one player . They have an 11 - game lead on the second - place Chicago Bulls , and they 're the only team in the NBA 

### Creates a Corpus For Each Key

Each corpus is just a string, this data-type was selected because it was easy to manipulate its values to conduct the tasks we wanted to perform.

- Cell 1) Creates the corpus for each team
- Cell 2) Stores data into each corpus

In [ ]:
Hawks_corpus = ""
Celtics_corpus = ""
Nets_corpus = ""
Hornets_corpus = ""
Bulls_corpus = ""
Cavaliers_corpus = ""
Mavericks_corpus = ""
Nuggets_corpus = ""
Pistons_corpus = ""
Warriors_corpus = ""
Rockets_corpus = ""
Pacers_corpus = ""
Clippers_corpus = ""
Lakers_corpus = ""
Grizzlies_corpus = ""
Heat_corpus = ""
Bucks_corpus = ""
Timberwolves_corpus = ""
Pelicans_corpus = ""
Knicks_corpus = ""
Thunder_corpus = ""
Magic_corpus = ""
Seventy_Sixers_corpus = ""
Suns_corpus = ""
Trail_Blazers_corpus = ""
Kings_corpus = ""
Spurs_corpus = ""
Raptors_corpus = ""
Jazz_corpus = ""
Wizards_corpus = ""

In [ ]:
for summary in home_team_dict["Hawks"]:
    Hawks_corpus += summary
    
for summary in home_team_dict["Celtics"]:
    Celtics_corpus += summary

for summary in home_team_dict["Nets"]:
    Nets_corpus += summary
    
for summary in home_team_dict["Hornets"]:
    Hornets_corpus += summary
    
for summary in home_team_dict["Bulls"]:
    Bulls_corpus += summary
    
for summary in home_team_dict["Cavaliers"]:
    Cavaliers_corpus += summary
    
for summary in home_team_dict["Mavericks"]:
    Mavericks_corpus += summary
    
for summary in home_team_dict["Nuggets"]:
    Nuggets_corpus += summary
    
for summary in home_team_dict["Pistons"]:
    Pistons_corpus += summary
    
for summary in home_team_dict["Rockets"]:
    Rockets_corpus += summary
    
for summary in home_team_dict["Pacers"]:
    Pacers_corpus += summary
    
for summary in home_team_dict["Warriors"]:
    Warriors_corpus += summary
    
for summary in home_team_dict["Clippers"]:
    Clippers_corpus += summary
    
for summary in home_team_dict["Lakers"]:
    Lakers_corpus += summary
    
for summary in home_team_dict["Grizzlies"]:
    Grizzlies_corpus += summary
    
for summary in home_team_dict["Heat"]:
    Heat_corpus += summary
    
for summary in home_team_dict["Bucks"]:
    Bucks_corpus += summary
    
for summary in home_team_dict["Timberwolves"]:
    Timberwolves_corpus += summary
    
for summary in home_team_dict["Pelicans"]:
    Pelicans_corpus += summary
    
for summary in home_team_dict["Knicks"]:
    Knicks_corpus += summary
    
for summary in home_team_dict["Thunder"]:
    Thunder_corpus += summary

for summary in home_team_dict["Magic"]:
    Magic_corpus += summary
    
for summary in home_team_dict["76ers"]:
    Seventy_Sixers_corpus += summary

for summary in home_team_dict["Suns"]:
    Suns_corpus += summary
    
for summary in home_team_dict["Trail Blazers"]:
    Trail_Blazers_corpus += summary
    
for summary in home_team_dict["Kings"]:
    Kings_corpus += summary
    
for summary in home_team_dict["Spurs"]:
    Spurs_corpus += summary
    
for summary in home_team_dict["Raptors"]:
    Raptors_corpus += summary
    
for summary in home_team_dict["Jazz"]:
    Jazz_corpus += summary
    
for summary in home_team_dict["Wizards"]:
    Wizards_corpus += summary

## Preparing the Data for the Model

For our project we generate a summary for Atlanta Hawks vs Charlotte Hornets games. We selected the Hornets because it is a team that both group members enjoy watching. The Hawks were selected because they play the Hornets three to four times every season.  

### Finds Hawks vs Hornets game in both the Hawks and Hornets Corpuses 

We had issues automating this part, it added several irrelevant summaries so we had to do it manually. 

#### Creates a list of all Summaries

We use two loops, one for the Hawks corpus and the other for the Hornets corpus

- Hawks Loop: Find all summaries that have the substring "Hornets" and add it to the list of potential corpuses.

- Hornets Loop: Find all summaries that have the substring "Hawks" and add it to the list of potential corpuses.

In [ ]:
potential_corpus = []

#counter = 1
for sum in home_team_dict["Hawks"]:
  if sum.find("Hornets") != -1:
    #print(counter,'\n', sum)
    #counter+=1
    potential_corpus.append(sum)

#counter = 1
for sum in home_team_dict["Hornets"]:
  if sum.find("Hawks") != -1:

    #print(counter,'\n', sum)
    #counter+=1
    potential_corpus.append(sum)

In [ ]:
counter = 0
for sum in potential_corpus:
  print(counter)
  print(sum)
  counter += 1

0
The Atlanta Hawks ( 32 - 27 ) handily defeated the Chicago Bulls ( 30 - 27 ) on Friday , 103 - 88 . Chicago was shorthanded , playing without Jimmy Butler , Derrick Rose , Nikola Mirotic , and Joakim Noah . For Atlanta , the win serves to end a slide in which the team went just 1 - 5 . The Hawks ' struggles did n't show on Friday , as they secured a decisive victory on the backs of their starting five 's solid offensive output . Point guard Jeff Teague led the team with 19 points while also dishing out nine assists . His scoring was nearly matched by All-Star center Al Horford , who scored 18 points on 8 - for - 11 shooting and blocked 4 shots . Atlanta swatted 12 shots as a team , including another five from All-Star power forward Paul Millsap . The team also found strength in the passing game , recording 28 team assits . Atlanta managed to force 20 turnovers , leading to 27 points on the other end . The Bulls have managed to stay fixed in the playoff picture despite the onslaught o

#### Adds Games to the Corpus

In [ ]:
corpus = ""
corpus += potential_corpus[1]
corpus += potential_corpus[2]
corpus += potential_corpus[3]
corpus += potential_corpus[9]
corpus += potential_corpus[13]
corpus += potential_corpus[16]
corpus += potential_corpus[21]
corpus += potential_corpus[23]
corpus += potential_corpus[33]
corpus += potential_corpus[37]
corpus += potential_corpus[38]

list_corpus = []
list_corpus.append(potential_corpus[1])
list_corpus.append(potential_corpus[2])
list_corpus.append(potential_corpus[3])
list_corpus.append(potential_corpus[9])
list_corpus.append(potential_corpus[13])
list_corpus.append(potential_corpus[16])
list_corpus.append(potential_corpus[21])
list_corpus.append(potential_corpus[23])
list_corpus.append(potential_corpus[33])
list_corpus.append(potential_corpus[37])
list_corpus.append(potential_corpus[38])

In [ ]:
corpus

"The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performances from several members of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 points , while Marco Belinelli matched his point total while playing 30 minutes off the bench . Kemba Walker returned from a one - game absence for personal reasons to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 points paced the Hawks , and Paul Millsap was right behind him with 20 points . Dennis Schroder registered 12 points , while Howard added 10 points , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A stron

In [ ]:
list_corpus

["The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performances from several members of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 points , while Marco Belinelli matched his point total while playing 30 minutes off the bench . Kemba Walker returned from a one - game absence for personal reasons to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 points paced the Hawks , and Paul Millsap was right behind him with 20 points . Dennis Schroder registered 12 points , while Howard added 10 points , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . ",
 "The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A

### Lemmatizes the Corpus

In [ ]:
from nltk.stem import WordNetLemmatizer 
temp = ""
lemmatizer = WordNetLemmatizer()

for word in word_tokenize(corpus):
  print(word, ':', lemmatizer.lemmatize(word))
  t = lemmatizer.lemmatize(word)
  temp+= " " + t

The : The
Hornets : Hornets
' : '
49 : 49
percent : percent
success : success
rate : rate
from : from
the : the
field : field
and : and
44 : 44
percent : percent
tally : tally
from : from
three : three
- : -
point : point
range : range
helped : helped
them : them
overcome : overcome
some : some
impressive : impressive
performances : performance
from : from
several : several
members : member
of : of
the : the
Hawks : Hawks
, : ,
including : including
a : a
23 : 23
- : -
rebound : rebound
effort : effort
from : from
Dwight : Dwight
Howard : Howard
. : .
Marvin : Marvin
Williams : Williams
equaled : equaled
a : a
season : season
high : high
with : with
19 : 19
points : point
, : ,
while : while
Marco : Marco
Belinelli : Belinelli
matched : matched
his : his
point : point
total : total
while : while
playing : playing
30 : 30
minutes : minute
off : off
the : the
bench : bench
. : .
Kemba : Kemba
Walker : Walker
returned : returned
from : from
a : a
one : one
- : -
game : game
absence : abse

In [ ]:
corpus

"The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performances from several members of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 points , while Marco Belinelli matched his point total while playing 30 minutes off the bench . Kemba Walker returned from a one - game absence for personal reasons to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 points paced the Hawks , and Paul Millsap was right behind him with 20 points . Dennis Schroder registered 12 points , while Howard added 10 points , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A stron

In [ ]:
temp

" The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performance from several member of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 point , while Marco Belinelli matched his point total while playing 30 minute off the bench . Kemba Walker returned from a one - game absence for personal reason to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 point paced the Hawks , and Paul Millsap wa right behind him with 20 point . Dennis Schroder registered 12 point , while Howard added 10 point , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A strong shootin

In [ ]:
corpus = temp
corpus

" The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performance from several member of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 point , while Marco Belinelli matched his point total while playing 30 minute off the bench . Kemba Walker returned from a one - game absence for personal reason to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 point paced the Hawks , and Paul Millsap wa right behind him with 20 point . Dennis Schroder registered 12 point , while Howard added 10 point , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A strong shootin

### Removes Some Punctuation

This helps us get rid of any unnessecray punctuation

In [ ]:
"""
  
#generated_summaries_set = {w for w in word_tokenize(str(generated_summaries)) if not w in sw}  
#human_summaries_set = {w for w in word_tokenize(str(list_corpus)) if not w in sw}  3

generated_summaries_NoStopWords = []
for i in range(len(generated_summaries)):
  temp = generated_summaries[i]
  temp_NoStopWords = {w for w in word_tokenize(str(temp)) if not w in sw}
  generated_summaries_NoStopWords.append(temp_NoStopWords)
""" 
temp = ""
for c in corpus:
  if c in string.punctuation:
    if c in [',', '(', ')', '-', '.', ':', "'"]:
      continue
    else:
      c = ''

In [ ]:
corpus

" The Hornets ' 49 percent success rate from the field and 44 percent tally from three - point range helped them overcome some impressive performance from several member of the Hawks , including a 23 - rebound effort from Dwight Howard . Marvin Williams equaled a season high with 19 point , while Marco Belinelli matched his point total while playing 30 minute off the bench . Kemba Walker returned from a one - game absence for personal reason to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - double of his own . Tim Hardaway , Jr. 's 21 point paced the Hawks , and Paul Millsap wa right behind him with 20 point . Dennis Schroder registered 12 point , while Howard added 10 point , an assist and a steal to his game - high rebound total . Kent Bazemore led the bench with a 17 - point total on 7 - of - 13 shooting . The Charlotte Hornets defeated the Atlanta Hawks , 107 - 99 , at Phillips Arena on Saturday . A strong shootin

### Finds the Average Length of a Summary and Sets max_length Value

This will allow us to generate a summary of an appropiate size. We added a runoff since each summary will not exactly be the average length. 

In [ ]:
avg_length = 0
total_length = 1
temp = 0
counter = 1

for summary in list_corpus:
  for word in word_tokenize(summary):
  #for c in summary:
    total_length += 1

  counter += 1

avg_length = total_length  / float(counter)
avg_length = int(avg_length)
#avg_length /=2
avg_length = int(avg_length)
avg_length

300

In [ ]:
runoff = 75

In [ ]:
max_length = avg_length + runoff
max_length = int(max_length)
max_length

375

## Sets Up Hyperparameters

In [ ]:
b_size = 350
n_epochs = 2
#starting_point = len(corpus) - max_length - 1
starting_point = avg_length #int(max_length/2)
step_size = 2
window = avg_length
text_diversity = 0.25
summary_length = avg_length*2

## Creates a Mapping for Characters and Indices

- Char → Index
- Index → Char

Key: 
- c: Character
- i: Index


In [ ]:
chars = sorted(list(set(corpus)))

char_indices = dict((c, i) for i, c in enumerate(chars))
indices_char = dict((i, c) for i, c in enumerate(chars))

In [ ]:
step = step_size
sentences = []
next_chars = []

for i in range(0, len(corpus) - max_length, step):
    sentences.append(corpus[i: i + max_length])
    next_chars.append(corpus[i + max_length])
    
x = np.zeros((len(sentences), max_length, len(chars)), dtype=np.bool)
y = np.zeros((len(sentences), len(chars)), dtype=np.bool)

for i, sentence in enumerate(sentences):
    for t, char in enumerate(sentence):
        x[i, t, char_indices[char]] = 1
    y[i, char_indices[next_chars[i]]] = 1

## Sets Up the Vocab 

In [ ]:
vocab = set(word_tokenize(corpus))
vocab_size = len(vocab)
num_chars = len(chars)
num_unique_chars = len(set(chars))

## Creates the RNN + LSTM Model

### Instantiates the Model, Adds Layers, Sets Up the Optimizer

#### Model
The model is a built using a Sequential Network. We chose Sequential because text is sequential data

#### Layers Used:
**LSTM**

**Dense**

**Dropout**

**GRU**

**Activation**

#### Optimizer:

**Adam**

In [ ]:
model = Sequential()

model.add(LSTM(256, input_shape=(max_length, len(chars)), return_sequences=True))
model.add(GRU(256, return_sequences=True))
#model.add(Dropout(0.5))
model.add(Dense(256))
model.add(Activation('softmax'))

model.add(LSTM(len(chars)*2, input_shape=(375, len(chars)*2), return_sequences=True))
model.add(GRU(len(chars)*2,  return_sequences=True))
model.add(Dropout(0.5))
model.add(Dense(len(chars)*2, activation=tf.nn.relu))
model.add(Activation('softmax'))

model.add(LSTM(len(chars), input_shape=(len(chars), 1), return_sequences=True)) 
model.add(GRU(len(chars)))
#model.add(Dropout(0.5))
model.add(Dense(len(chars), activation=tf.nn.relu))
model.add(Activation('softmax'))

optimizer = Adam(learning_rate=0.01)
model.compile(loss='categorical_crossentropy', optimizer=optimizer)  

### Model Summary

In [ ]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_3 (LSTM)                (None, 375, 256)          331776    
_________________________________________________________________
gru_3 (GRU)                  (None, 375, 256)          394752    
_________________________________________________________________
dense_3 (Dense)              (None, 375, 256)          65792     
_________________________________________________________________
activation_3 (Activation)    (None, 375, 256)          0         
_________________________________________________________________
lstm_4 (LSTM)                (None, 375, 134)          209576    
_________________________________________________________________
gru_4 (GRU)                  (None, 375, 134)          108540    
_________________________________________________________________
dropout_1 (Dropout)          (None, 375, 134)         

### Methods For the Model

#### Helper Methods

##### sample
- Helps us sample an inde from an array of probailities

##### on_end_of_epoch
- Called at the end of every epoch
- Prints the text the model generated

In [ ]:
def sample(predictions, temperature=1.0):
    predictions = np.asarray(predictions).astype('float64')
    predictions = np.log(predictions) / temperature
    
    exp_predictions = np.exp(predictions)
    
    predictions = exp_predictions / np.sum(exp_predictions)
    
    probabilities = np.random.multinomial(1, predictions, 1)
    
    return np.argmax(probabilities)


def on_end_of_epoch(epoch, logs):
    print()
    print('----- Generating text after Epoch: %d' % epoch)
    
    start_index = random.randint(0, len(corpus) - max_length - 1)
    for diversity in [0.2, 0.5, 1.0, 1.2]:
        print('----- diversity:', diversity)

        generated = ''
        sentence = text[start_index: start_index + max_length]
        generated += sentence
        print('----- Generating with seed: "' + sentence + '"')
        sys.stdout.write(generated)
        
        for i in range(400):
            x_prediction = np.zeros((1, maxlen, len(chars)))
            for t, char in enumerate(sentence):
                x_prediction[0, t, char_indices[char]] = 1.0
                
            predictions= model.predict(x_prediction, verbose=0)[0]
            next_index = sample(predictions, diversity)
            next_char = indices_char[next_index]
            
            generated += next_char
            sentence = sentence[1:] + next_char
            
            sys.stdout.write(next_char)
            sys.stdout.flush()
        
        print()
        

print_callback = LambdaCallback(on_end_of_epoch=on_end_of_epoch)

#### Callback Functions

##### 1) Helps us save the model after each epoch the loss is decreased

##### 2) Reduces the Learning Rate each time the model's learning begins to plateau

In [ ]:
filepath = "weights.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss',
                             verbose=1, save_best_only=True,
                             mode='min')

In [ ]:
reduce_lr = ReduceLROnPlateau(monitor='loss', factor=0.2,
                              patience=1, min_lr=0.001)
callbacks = [print_callback, checkpoint, reduce_lr]

## Trains the Model

In [ ]:
model.fit(x, y, batch_size=b_size, epochs=n_epochs, callbacks=callbacks)

Epoch 1/2
20/20 [==============================] - ETA: 0s - loss: 3.4065 
Epoch 00001: loss improved from inf to 3.40655, saving model to weights.hdf5
20/20 [==============================] - 470s 23s/step - loss: 3.4065
Epoch 2/2
20/20 [==============================] - ETA: 0s - loss: 3.4039 
Epoch 00002: loss improved from 3.40655 to 3.40388, saving model to weights.hdf5
20/20 [==============================] - 469s 23s/step - loss: 3.4039


## Generate a Summary

In [ ]:
def generate_summary(length, diversity, starting_point):

  # Random Start
  start_index = random.randint(0, len(corpus) - avg_length - 1)
  generated = ''
  sentence = corpus[start_index: start_index + avg_length]
  generated += sentence

  for i in range(length):
    x_prediction = np.zeros((1, avg_length, len(chars)))
    for t, char in enumerate(sentence):
                x_prediction[0, t, char_indices[char]] = 1.0

    predictions = model.predict(x_prediction, verbose=0)[0]
    next_index = sample(predictions, diversity)
    next_char = indices_char[next_index]

    generated += next_char
    sentence = sentence[1:] + next_char
  
  generated = generated[:length]
  return generated

In [ ]:
#summary = generate_summary(avg_length, text_diversity, starting_point)
summary = generate_summary(avg_length, text_diversity, starting_point)
print(summary)

nday . For Atlanta , the win is the second straight after a three - game losing streak ended on Friday . No player scored over 14 points , but five Hawks reached double - digits on Sunday . Forward Kent Bazemore led the way with 14 , also chipping in six rebounds and three assists . Center Al Horfor


In [ ]:
# Lists of generated summaries
generated_summaries = []
limit = len(list_corpus)
for i in range(limit):
  generated_summaries.append(generate_summary(avg_length, text_diversity, starting_point))
  print("Generated Summary #" + str(i+1))
  print(generated_summaries[i] + '\n')

Generated Summary #1
gh with 19 points , while Marco Belinelli matched his point total while playing 30 minutes off the bench . Kemba Walker returned from a one - game absence for personal reasons to post an 18 - point , 10 - assist double - double , while Cody Zeller fashioned a 16 - point , 11 - rebound double - doubl

Generated Summary #2
he bench for Charlotte , as he poured in 19 points and went 8 - for - 8 from the free - throw line . With center Al Jefferson ( meniscus ) still out , Cody Zeller was able to shine in his starting role , posting a 19 - point , 10 - rebound double - double along with three blocks . The Hornets simply

Generated Summary #3
 losing streak ended on Friday . No player scored over 14 points , but five Hawks reached double - digits on Sunday . Forward Kent Bazemore led the way with 14 , also chipping in six rebounds and three assists . Center Al Horford , meanwhile , made a noteworthy contribution with 16 rebounds and six 

Generated Summary #4
trength Sa

## Metrics

### BLEU
Uses the `corpus_bleu()` method to evaluate our text

In [ ]:
smooth = SmoothingFunction().method7
score = corpus_bleu(list_corpus, generated_summaries, smoothing_function=smooth)
print(score)

0.3862532679943824


### ROUGE

Uses the `rougeLsum` metric in the `RougeScorer()` method to evaluate our text

In [ ]:
counter = 0
avg_precision = 0
avg_recall = 0
avg_fmeasure = 0

total_precision = 0
total_recall = 0
total_fmeasure = 0

for i in range(limit):
  scorer = rouge_scorer.RougeScorer(['rougeLsum'], use_stemmer=True)
  scores = scorer.score(str(list_corpus[i]), str(generated_summaries[i]))
  print(scores)

  for key, val in scores.items():
    total_precision += val.precision
    total_recall += val.recall
    total_fmeasure += val.fmeasure

  counter+=1

{'rougeLsum': Score(precision=0.9795918367346939, recall=0.3221476510067114, fmeasure=0.4848484848484848)}
{'rougeLsum': Score(precision=0.36538461538461536, recall=0.06312292358803986, fmeasure=0.10764872521246457)}
{'rougeLsum': Score(precision=0.22916666666666666, recall=0.06790123456790123, fmeasure=0.10476190476190475)}
{'rougeLsum': Score(precision=0.39215686274509803, recall=0.07246376811594203, fmeasure=0.12232415902140673)}
{'rougeLsum': Score(precision=0.9622641509433962, recall=0.24170616113744076, fmeasure=0.3863636363636364)}
{'rougeLsum': Score(precision=0.3584905660377358, recall=0.06129032258064516, fmeasure=0.1046831955922865)}
{'rougeLsum': Score(precision=0.9074074074074074, recall=0.13920454545454544, fmeasure=0.24137931034482754)}
{'rougeLsum': Score(precision=0.28, recall=0.03713527851458886, fmeasure=0.06557377049180327)}
{'rougeLsum': Score(precision=0.3157894736842105, recall=0.0703125, fmeasure=0.11501597444089458)}
{'rougeLsum': Score(precision=0.224137931034

In [ ]:
avg_precision = total_precision / float(counter)
avg_recall = total_recall / float(counter)
avg_fmeasure = total_fmeasure / float(counter)
print("Average rogueLsum Scores:")
print("\t",avg_precision)
print("\t",avg_recall)
print("\t",avg_fmeasure)

Average rogueLsum Scores:
	 0.48204773671442247
	 0.10662633347243414
	 0.17237674585070265
